<h1><center> Automatic Differentiation with AutoGrad</center></h1>


### Introduction
In machine learning, we *train* models to get better and bettter as a function of experience. Usually, *getting better* means minimizing a *loss* function, i.e. a score that answers "how *bad* is our model?" With neural networks, we choose loss functions to be differentiable with respect to our parameters. Put simply, this means that for each of the model's parameters, we can determine how much *increasing* or *decreasing* it might affect the loss. While the calculations are straighforward, for complex models, working it out by hand can be a pain. 

Knet relies on the [AutoGrad](https://github.com/denizyuret/AutoGrad.jl) package to compute the gradient of Julia functions. While most other libraries require that we compile a symbolic graph to take automatic derivaties, AutoGrad, like mxnet.autograd and PyTorch, allows you to take derivaties while writing ordinary imperative code. Every time you make a pass through your model, AutoGrad builds a graph on the fly, thorough which it can immediately backpropagate gradients. Formally, high-level languages, like Julia and Python, already know how to decompose functions into their elementary operations. If we let the users define their models directly in a high-level language, then record the elementary operations during loss calculation at run-time, a dynamic computational graph can be constructed from the recorded operations. This is the approach taken by the popular [autograd](https://github.com/HIPS/autograd) Python package and its Julia port AutoGrad.jl used by Knet.

Let's go through it step by step. For this tutorial, we'll only need to use AutoGrad:

In [1]:
using AutoGrad

### Broadcasting

As a toy example, let's say that we are interested in differentiating a function $f = 2x^2$ with respect to parameter $x$. We can start by assigning an initial value of x and defining the function f(x):  

In [44]:
x    = [1 2; 3 4];
f(x) = 2x^2;

In Knet g=grad(f) generates a gradient function g, which takes the same inputs as the function f but returns the gradient. The gradient function g triggers recording by boxing the parameters in a special data type and calls f. The elementary operations in f are overloaded to record their actions and output boxed answers when their inputs are boxed. The sequence of recorded operations is then used to compute gradients.

In [38]:
g = grad(f)

(::gradfun) (generic function with 1 method)

Note that grad requires a scalar-valued function, i.e. f(x) = c for some constant $c$. We may evaluate g at x = 2 simply as g(x). However, doing so as such for non-scalars such as x = [1 2; 3 4] will raise and error. To compute the piecewise gradients we need to broadcast g: 

In [45]:
g.(x)

2×2 Array{Float64,2}:
  4.0   8.0
 12.0  16.0

Since $g(x) = df(x)/dx = 4x$ we see that our results are as expected.

### Chain Rule

Recall that a function $f_1(x)$ is an *explicit* function of $x$ if it depends directly on $x$, e.g. $f_1(x)=2x^2$. On the other hand, if $f_2(x)$ is an *implicit* function of $x$, this means that $f_2$ depends on a variable which itself depends on $x$, e.g. $f_2(y)= 2 y$ such that $y=f_1(x)$. Implicit differentiation makes use of the chain rule to differentiate implicitly defined functions: 

\begin{equation}
\frac{d f_2(y)}{d x} = \frac{d f_2(y)}{d y}\frac{d y}{d x}=\frac{d f_2(y)}{d y}\frac{d f_1(x)}{d x}
\end{equation}

<h1><center> Advanced Discussion</center></h1>

### Broadcasting

Let's consider a more complex function to illustrate element-wise differentiation. Consider the function $f(x,y)$ defined as:

\begin{equation}
f(x,y) = \Big (\|x\|^2\|y\|^2 - (x \cdot y) ^2\Big)^{1/2}
\end{equation}

Suppose that we want to evaluate the gradient of $f$ with respect to $x$, i.e. 

\begin{equation}
\frac{d}{dx}f(x,y) = \frac{\big( x \|y\|^2 - y(x \cdot y) \big)}{f(x,y) ^{1/2}}
\end{equation}

In this case we need to be careful about the norm since n-element arrays can be used as an input. Then, we define our function in terms of what we define is a single element input. As an example, suppose that $x, y\in \mathbb{R}^3$. In this case:

In [56]:
using AutoGrad

normSquared(x)   = sum(x .^ 2)
dotSquared(x, y) = sum(x .* y) .^ 2
f(x, y)          = sqrt(normSquared(x) * normSquared(y) - dotSquared(x, y))
fgrad            = grad(f)

(::gradfun) (generic function with 1 method)

In [63]:
x = [1.0,2.0,0.0];
y = [3.0,1.0,0.0];

fgrad(x, y) == (x * normSquared(y) - y * (dotSquared(x, y) ^ 0.5)) / f(x, y)

true

Now that our model works for a "single element" we can introduce broadcasting for multiple elements $x_i, y_i\in \mathbb{R}^3$ for i=1,2,3,4:

In [68]:
x = [[1.0,2.0,0.0], [0.0,-1.0,0.0], [0.5,-2.0,1.0], [0.9,-2.0,1.0]];
y = [[3.0,1.0,0.0], [-2.0,0.0,0.0], [1.0,-4.0,0.0], [0.5,-2.0,1.0]];

In [69]:
fgrad.(x, y)

4-element Array{Array{Float64,1},1}:
 [-1.0, 3.0, 0.0]              
 [0.0, -2.0, 0.0]              
 [0.0, 0.0, 4.12311]           
 [2.23607, 0.447214, -0.223607]

You can verify that the gradients for the other elements $i=2,3,4$ are correct. 

### Chain Rule

Let's take a closer look at what's under the hood of the grad(f) function. Once again we will consider the function $f(x)=2x^2$ and we will start with the scalar value $x=2$. 

In [15]:
x    = 2; 
y(x) = 2x; 
z(x) = y(x) * x;

Roughly, the steps performed by g(x), where g = grad(f) are as follow:

1. g is called with the same inputs as f.
2. g calls forward_pass which boxes x in a Rec type and calls f(Rec(x)).
3. If a primitive operator inside f gets a Rec input, it records its action and returns a Rec output.
4. g calls backward_pass which returns the gradient df/dx.

It's important to note that only one of the regular args is the gradient target, specified by the argnum argument of grad (defaults to 1). Thus, if f = f(x,y,...) is a multi-variable function, grad(f) will take the gradient only with respect to (wrt) the one argument. To specity the derivative wrt y we call grad(f, argnum=2). 

In [49]:
function f1(w, x)
    print("accessing f1 \n")
    return w * x
end
f2(w, x) = w * x + 1

f2 (generic function with 2 methods)

In [50]:
gradf2 = grad(f2)

(::gradfun) (generic function with 1 method)

In [51]:
function train(w, x)
    z = f1(w, x)
     
    return gradf2(w, z)
end

train (generic function with 1 method)

In [52]:
train(2, 3)

accessing f1 


6

In [53]:
gradf2(2, 6)

6